In [216]:
import pandas as pd
import numpy as np
import xgboost as xgb
from sklearn.metrics import roc_auc_score
from xgboost import XGBClassifier
from sklearn.model_selection import KFold
from scipy.interpolate import lagrange
import matplotlib.pyplot as plt
from sklearn.linear_model import LogisticRegressionCV,LinearRegression
from sklearn.linear_model.logistic import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import GridSearchCV
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from sklearn import metrics
from collections import Counter
from imblearn.over_sampling import RandomOverSampler,SMOTENC
from imblearn.under_sampling import RandomUnderSampler
from imblearn.under_sampling import TomekLinks
import pandas as pd
import numpy as np
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import KFold
from scipy.interpolate import lagrange
import matplotlib.pyplot as plt
from sklearn.linear_model import LogisticRegressionCV,LinearRegression
from sklearn.linear_model.logistic import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import GridSearchCV
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from sklearn import metrics
from collections import Counter
from imblearn.over_sampling import RandomOverSampler,SMOTE,SMOTENC
from imblearn.under_sampling import RandomUnderSampler
from imblearn.under_sampling import TomekLinks
import warnings
warnings.filterwarnings(module='sklearn*', action='ignore', category=DeprecationWarning)
from catboost import CatBoostClassifier
import random
import lightgbm as lgb
from sklearn.neighbors import NearestNeighbors

In [217]:
place = 'try2.txt'
train = pd.read_csv(place, sep='\t')
print(train.shape)

(18618, 39)


In [218]:
train = train.dropna(axis=0)

In [219]:
train.index = list(range(7939))

In [220]:
fea = train['性别']
A1 = fea[fea==1]; B1 = A1.index
A2 = fea[fea==0]; B2 = A2.index
X1 = train.iloc[B1, :]
X2 = train.iloc[B2, :]
X1['VAI'] = (X1['腰围']/(39.68+1.88*X1['体重指数'])) * (X1['甘油三酯']/1.03)*(1.31/X1['高密度脂蛋白'])
X2['VAI'] = (X2['腰围']/(36.58+1.89*X2['体重指数'])) * (X2['甘油三酯']/0.81)*(1.52/X2['高密度脂蛋白'])
train = pd.concat([X1,X2], axis=0)

D:\anaconda\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
D:\anaconda\lib\site-packages\ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys


In [221]:
#train["白红计数比"] = train["白细胞总数"]/train["红细胞总数"]
#train["红细胞总体积"] = train["平均红细胞体积"]*train["红细胞总数"]
#train['肾'] = train['肌酐'] + train['尿酸'] + train['尿素氮']
#train['总酶'] = train['谷草转氨酶'] + train['谷丙转氨酶']
#train['谷草酶ratio'] = train['谷草转氨酶']/np.maximum(train["总酶"].astype("float"),1)
#train['谷丙酶ratio'] = train['谷丙转氨酶']/np.maximum(train["总酶"].astype("float"),1)
#train['总蛋白'] = train["高密度脂蛋白"] + train["低密度脂蛋白"] + train['血红蛋白']
train['谷丙草比']=train['谷丙转氨酶']/train['谷草转氨酶']
train['高低蛋白比'] =  train["高密度脂蛋白"]/train["低密度脂蛋白"]
#train['谷丙草比lg']=np.log(train['谷丙转氨酶']/train['谷草转氨酶'])
train['非高密度脂蛋白'] = train['总胆固醇'] - train['高密度脂蛋白']#这个确实很有用0.002
#train['高密度脂蛋白胆固醇ratio'] = train['高密度脂蛋白']/np.maximum(train["总胆固醇"].astype("float"),1) 
#train['低密度脂蛋白胆固醇ratio'] = train['低密度脂蛋白']/np.maximum(train["总胆固醇"].astype("float"),1)
#train['甘三胆固比'] = train['甘油三酯']*train['总胆固醇']#有用0.006
#train['低高蛋白比'] = train["低密度脂蛋白"]/train["高密度脂蛋白"]#有用0.004
#train['低密度胆固比'] = train["低密度脂蛋白"]/train["总胆固醇"]
#train['甘三低蛋白差'] = train["低密度脂蛋白"]-train['甘油三酯']#有用0.004
#train['甘三高蛋白比'] = train["高密度脂蛋白"]-train['甘油三酯']
#train['非低密度脂蛋白'] = train['总胆固醇'] - train['低密度脂蛋白']

In [222]:
#改变右长尾分布
for column in train.columns:

    if len(train[column].unique()) > 10 and train[column].mean() > 1:

        skew = train[column].skew()

        if abs(skew) > 1.0 and train[column].min() > -1:

            train[column] = np.log1p(train[column])

In [223]:
y = train['fld']
train = train.drop(['fld'],axis=1)
print(np.sum(y==0))
print(np.sum(y==1))

6992
947


In [224]:
X = np.array(train)
y = np.array(y)

In [225]:
auc_best = 0
best = []
for num_leaves in range(20,35):
    for class_weight in range(9,14):
        for reg_alpha in range(15,25):
            for reg_lambda in range(10,25):
                for min_child_samples in range(1,20):
                    skf = StratifiedKFold(n_splits=10,random_state=0,shuffle=True)
                    clf = lgb.LGBMClassifier(class_weight={1:class_weight,0:1},categorical_features=[0,36,37],
                                             colsample_bytree=0.8,num_leaves=num_leaves,reg_alpha=reg_alpha,
                                             reg_lambda=reg_lambda ,min_child_samples=min_child_samples,
                                             eval_metric=auc)
                    score1 = []
                    score2 = []
                    Sensitivity = []
                    Specificity = []
                    auc = []
                    for train, test in skf.split(X,y):
                        X_train,X_test=X[train],X[test]
                        y_train,y_test=y[train],y[test]
                        clf.fit(X_train, y_train)

                        y_pred1 = clf.predict(X_train)
                        accuracy1 = np.mean(y_train==y_pred1)
                        score1.append(accuracy1)

                        y_pred2 = clf.predict(X_test)
                        accuracy2 = np.mean(y_test==y_pred2)
                        score2.append(accuracy2)
                        confusion = metrics.confusion_matrix(y_test, y_pred2)
                        auc_ = metrics.roc_auc_score(y_test, y_pred2)
                        TP = confusion[1, 1]
                        TN = confusion[0, 0]
                        FP = confusion[0, 1]
                        FN = confusion[1, 0]
                        TPR = TP/(TP+FN)
                        TNR = TN/(TN+FP)
                        Sensitivity.append(TPR)
                        Specificity.append(TNR)
                        auc.append(auc_)
                    score1 = np.array(score1)
                    score2 = np.array(score2)
                    Sensitivity = np.array(Sensitivity)
                    Specificity = np.array(Specificity)
                    auc = np.array(auc)
                    if np.mean(auc) > auc_best:
                        best = []
                        auc_better = auc
                        best.append(num_leaves)
                        best.append(reg_alpha)
                        best.append(reg_lambda)
                        best.append(class_weight)
                        best.append(min_child_samples)
                        best.append(np.mean(auc))
                    print('The accuracy on trainging set is:',np.mean(score1),'The accuracy on test set is:', np.mean(score2))
                    print('The Sensitivity is:', np.mean(Sensitivity), 'The Specificity is', np.mean(Specificity))
                    print('num_leaves is:',num_leaves,'reg_alpha is:',reg_alpha,'reg_lambda is:',reg_lambda,'class_weight',class_weight,'min_child_samples is:',min_child_samples,'auc is:', np.mean(auc))

The accuracy on trainging set is: 0.843865033507976 The accuracy on test set is: 0.7844805642675375
The Sensitivity is: 0.7412765957446809 The Specificity is 0.7903325158389536
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 10 class_weight 9 min_child_samples is: 1 auc is: 0.7658045557918172
The accuracy on trainging set is: 0.8438230617643757 The accuracy on test set is: 0.7847311864689647
The Sensitivity is: 0.7507502799552073 The Specificity is 0.7893300633558143
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 10 class_weight 9 min_child_samples is: 2 auc is: 0.7700401716555109
The accuracy on trainging set is: 0.8436971132590539 The accuracy on test set is: 0.783850684123407
The Sensitivity is: 0.7539417693169093 The Specificity is 0.7879004700592683
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 10 class_weight 9 min_child_samples is: 3 auc is: 0.7709211196880889
The accuracy on trainging set is: 0.8444389044449881 The accuracy on test set is: 0.7854859014523558
The Sensit

The accuracy on trainging set is: 0.843977039086868 The accuracy on test set is: 0.786872404422527
The Sensitivity is: 0.7528667413213885 The Specificity is 0.7914761904761904
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 11 class_weight 9 min_child_samples is: 10 auc is: 0.7721714658987895
The accuracy on trainging set is: 0.8442148971971768 The accuracy on test set is: 0.7852376607579681
The Sensitivity is: 0.7444120940649495 The Specificity is 0.7907627222562844
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 11 class_weight 9 min_child_samples is: 11 auc is: 0.767587408160617
The accuracy on trainging set is: 0.8444108697510698 The accuracy on test set is: 0.7851117165731335
The Sensitivity is: 0.7496864501679731 The Specificity is 0.7899047619047619
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 11 class_weight 9 min_child_samples is: 12 auc is: 0.7697956060363675
The accuracy on trainging set is: 0.8436271127136361 The accuracy on test set is: 0.7824656097378206
The Sens

The accuracy on trainging set is: 0.8426754021374064 The accuracy on test set is: 0.7863718004954359
The Sensitivity is: 0.7465173572228443 The Specificity is 0.7917625178826896
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 12 class_weight 9 min_child_samples is: 19 auc is: 0.7691399375527671
The accuracy on trainging set is: 0.842647434037492 The accuracy on test set is: 0.786621944637443
The Sensitivity is: 0.7507278835386338 The Specificity is 0.7914763948497854
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 13 class_weight 9 min_child_samples is: 1 auc is: 0.7711021391942097
The accuracy on trainging set is: 0.8418497987211447 The accuracy on test set is: 0.7844804098421586
The Sensitivity is: 0.7518253079507279 The Specificity is 0.7889012875536481
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 13 class_weight 9 min_child_samples is: 2 auc is: 0.7703632977521879
The accuracy on trainging set is: 0.8416396932427894 The accuracy on test set is: 0.7822135641459351
The Sensi

The accuracy on trainging set is: 0.8404502401364956 The accuracy on test set is: 0.7839763122656163
The Sensitivity is: 0.7571444568868981 The Specificity is 0.7876137339055794
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 14 class_weight 9 min_child_samples is: 9 auc is: 0.7723790953962387
The accuracy on trainging set is: 0.8414018880254044 The accuracy on test set is: 0.783221436464075
The Sensitivity is: 0.7603023516237403 The Specificity is 0.7863280196198651
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 14 class_weight 9 min_child_samples is: 10 auc is: 0.7733151856218028
The accuracy on trainging set is: 0.8416677553602515 The accuracy on test set is: 0.7841033677937661
The Sensitivity is: 0.7581746920492721 The Specificity is 0.7876143470263642
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 14 class_weight 9 min_child_samples is: 11 auc is: 0.7728945195378182
The accuracy on trainging set is: 0.8410240288220665 The accuracy on test set is: 0.7830966044216521
The Sen

The accuracy on trainging set is: 0.840422117285328 The accuracy on test set is: 0.7838529068100374
The Sensitivity is: 0.7517693169092945 The Specificity is 0.7881874105865521
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 15 class_weight 9 min_child_samples is: 18 auc is: 0.7699783637479233
The accuracy on trainging set is: 0.840576073065959 The accuracy on test set is: 0.7813314735962867
The Sensitivity is: 0.7528107502799551 The Specificity is 0.7851831187410586
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 15 class_weight 9 min_child_samples is: 19 auc is: 0.768996934510507
The accuracy on trainging set is: 0.8395403210739116 The accuracy on test set is: 0.7838492567374664
The Sensitivity is: 0.7549720044792833 The Specificity is 0.7877574085428163
num_leaves is: 20 reg_alpha is: 15 reg_lambda is: 16 class_weight 9 min_child_samples is: 1 auc is: 0.7713647065110497
The accuracy on trainging set is: 0.8394423602512667 The accuracy on test set is: 0.7822132453064723
The Sensi

...

The accuracy on trainging set is: 0.8402962549699323 The accuracy on test set is: 0.787124137168173
The Sensitivity is: 0.7612877939529674 The Specificity is 0.7906163907623136
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 18 class_weight 9 min_child_samples is: 9 auc is: 0.7759520923576406
The accuracy on trainging set is: 0.8398903316867437 The accuracy on test set is: 0.784356683549376
The Sensitivity is: 0.7602463605823069 The Specificity is 0.7876153688943388
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 18 class_weight 9 min_child_samples is: 10 auc is: 0.7739308647383228
The accuracy on trainging set is: 0.8392324859185967 The accuracy on test set is: 0.7858686558413478
The Sensitivity is: 0.7591937290033595 The Specificity is 0.789474351113836
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 18 class_weight 9 min_child_samples is: 11 auc is: 0.7743340400585979
The accuracy on trainging set is: 0.8391765516817049 The accuracy on test set is: 0.7866208328945794
The Sensi

The accuracy on trainging set is: 0.8383087630354614 The accuracy on test set is: 0.7825918723625699
The Sensitivity is: 0.7507950727883539 The Specificity is 0.7868994481912936
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 19 class_weight 9 min_child_samples is: 18 auc is: 0.7688472604898238
The accuracy on trainging set is: 0.8391486090533637 The accuracy on test set is: 0.7807012726149525
The Sensitivity is: 0.7454759238521835 The Specificity is 0.7854696505211527
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 19 class_weight 9 min_child_samples is: 19 auc is: 0.7654727871866681
The accuracy on trainging set is: 0.8392743871373843 The accuracy on test set is: 0.7841041602976186
The Sensitivity is: 0.7486114221724522 The Specificity is 0.7889027181688126
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 20 class_weight 9 min_child_samples is: 1 auc is: 0.7687570701706326
The accuracy on trainging set is: 0.837511108122644 The accuracy on test set is: 0.781077840599407
The Sens

The accuracy on trainging set is: 0.8381548385905407 The accuracy on test set is: 0.7801989252592952
The Sensitivity is: 0.7528331466965285 The Specificity is 0.7838963825873698
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 21 class_weight 9 min_child_samples is: 8 auc is: 0.7683647646419491
The accuracy on trainging set is: 0.8382947966130064 The accuracy on test set is: 0.7849859324073524
The Sensitivity is: 0.7570884658454647 The Specificity is 0.7887594522787655
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 21 class_weight 9 min_child_samples is: 9 auc is: 0.7729239590621152
The accuracy on trainging set is: 0.8378189432861834 The accuracy on test set is: 0.7814583723017685
The Sensitivity is: 0.7517805151175813 The Specificity is 0.7854698548947476
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 21 class_weight 9 min_child_samples is: 10 auc is: 0.7686251850061644
The accuracy on trainging set is: 0.8376089984199281 The accuracy on test set is: 0.7830943821345698
The Sen

The accuracy on trainging set is: 0.838238893719501 The accuracy on test set is: 0.7839780556941822
The Sensitivity is: 0.7612877939529674 The Specificity is 0.7870439403229103
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 22 class_weight 9 min_child_samples is: 17 auc is: 0.7741658671379389
The accuracy on trainging set is: 0.8384488620784918 The accuracy on test set is: 0.7836019689655332
The Sensitivity is: 0.7528667413213885 The Specificity is 0.7877586347843859
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 22 class_weight 9 min_child_samples is: 18 auc is: 0.7703126880528872
The accuracy on trainging set is: 0.8377910143572775 The accuracy on test set is: 0.783473166812432
The Sensitivity is: 0.7465061590145576 The Specificity is 0.7884735336194564
num_leaves is: 21 reg_alpha is: 17 reg_lambda is: 22 class_weight 9 min_child_samples is: 19 auc is: 0.767489846317007
The accuracy on trainging set is: 0.8354956500374883 The accuracy on test set is: 0.7820885688880728
The Sens

KeyboardInterrupt: 